# Solis Setup

This is a simple script for connecting to STK through the Python object model interface and connecting to Solis

Before running this notebook, you must first update the USE_SOLIS parameter in config.json to True and then run configure.py to set up the python virtual environment with the required dependencies. Note that the Solis programmatic interface is only supported on Windows.

In [ ]:
from agi.stk12.stkdesktop import STKDesktop
from agi.stk12.stkengine import STKEngine
from agi.stk12.stkobjects import *
from agi.stk12.utilities.colors import *
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib
import os
import sys
from scipy.spatial import ConvexHull
import socket
import platform
import json
import time
 
socket.gethostname()
# Solis specific imports
import clr
clr.AddReference('C:/Program Files/AGI/STK 12/Solis/bin/STKSolisLib.dll') # Load the DLL
from STKSolis import SolisConnect # type: ignore

RUN_HEADLESS = False

if RUN_HEADLESS :
    stk = STKEngine.StartApplication(noGraphics=False)
    stkRoot = stk.NewObjectRoot()
else :
    # An existing STK instance must be running!
    stk = STKDesktop.AttachToApplication()
    if stk:
        print("Connected")
    else:
        print("Not Connected")
    stkRoot = stk.Root
    print(stkRoot)

scenario = stkRoot.CurrentScenario
print(scenario)
scenario.SetTimePeriod('1 Jan 2024 17:10:00.000', '2 Jan 2024 22:00:00.000')
stkRoot.Rewind()
 

scenario.VO.SurfaceReference = AgESurfaceReference.eMeanSeaLevel
scenario.Animation.AnimStepValue = 1.0


obj = SolisConnect() # Connect to SOLIS
satNames = list(obj.SatelliteNames)
print(satNames) # Check what Satellites are in scenario
sat_solis = obj.GetSatellite(satNames[0]) # Get Landmapper_BC satellite

s = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)
s2 = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)

client = '10.55.21.3'
client2 = "10.55.11.44"
port = 5005
port2 = 5004
print(f"Client = {client},{port}")
print(f"Client = {client2},{port2}")

config = sat_solis.GetConfiguration()
try:
    config.RunRealTime()
except Exception as e:
    print(e)
sat = scenario.Children.Item("SAT1")
dataProvider = sat.DataProviders.Item("User Supplied Data")
solisFolder = dataProvider.Group.Item("SOLIS Simulation")
dynamicsFolder = dataProvider.Group.Item("ODySSy Dynamics")
fluxFolder = dataProvider.Group.Item("ODySSy Power Thermal")
rollFolder = dataProvider.Group.Item("ODySSy Actuator Model")
gpsFolder = dataProvider.Group.Item('ODySSy Sensor Model')

# Note-- these need to be in the correct order per SOLIS TLM GUI page per subcategory
dynamics = ["Time", "ODY EOM Summary Pos_CBIX","ODY EOM Summary Pos_CBIY","ODY EOM Summary Pos_CBIZ",
            "ODY EOM Summary SCRate_BDYX",
            "ODY EOM Summary SCRate_BDYY",
            "ODY EOM Summary SCRate_BDYZ",
            'ODY EOM Summary Vel_CBIX',"ODY EOM Summary Vel_CBIY","ODY EOM Summary Vel_CBIZ" 
            ]

gps = ['ODY GPS MeasValid','ODY GPS Pos_CBFX', 'ODY GPS Pos_CBFY', 'ODY GPS Pos_CBFZ', 'ODY GPS Time',  'ODY GPS Vel_CBFX', 'ODY GPS Vel_CBFY', 'ODY GPS Vel_CBFZ' ]
 
solis = ["STK BattSOC",'STK Eclipse', 'STK GenPower', 'STK LoadPower', 'STK ModeString']

#solis = ["STK BattCurr","STK BattSOC","STK BattVolt","STK Eclipse", "STK GenPower", "STK LoadPower","STK ModeString"]
flux = ["ODY Panel SolarFlux SolarFluxSA_A_PZ","ODY Panel SunAngle SunAngleSA_A_PZ"]
roll = ["ODY SA_B_NZ GimbalRate", "ODY SA_A_PZ GimbalRate"]

everything = dynamics + solis + flux + roll + gps

while True:
    try:
        #data = powerFolder.ExecElements(scenario.StartTime,scenario.StopTime,1.0,["Time","STK BattSOC","STK BattCurr (A)"])
        dyndata = dynamicsFolder.ExecElements(scenario.StartTime, scenario.StopTime, 1.0, dynamics)
        dynArray = dyndata.DataSets.ToNumpyArray()
        solisdata = solisFolder.ExecElements(scenario.StartTime, scenario.StopTime, 1.0, solis)
        solisArray = solisdata.DataSets.ToNumpyArray()
        fluxdata = fluxFolder.ExecElements(scenario.StartTime, scenario.StopTime, 1.0, flux)
        fluxarray = fluxdata.DataSets.ToNumpyArray()
        rolldata = rollFolder.ExecElements(scenario.StartTime, scenario.StopTime, 1.0, roll)
        rollarray = rolldata.DataSets.ToNumpyArray()
        gpsdata=gpsFolder.ExecElements(scenario.StartTime, scenario.StopTime, 1.0, gps)
        gpsarray = gpsdata.DataSets.ToNumpyArray()
        dataLength = len(dynArray)
        solisLength = len(solisArray)
        fluxLength = len(fluxarray)
        rollLength = len(rollarray)
        gpslength = len(gpsarray)

        value = np.concatenate((dynArray[dataLength - 1],  solisArray[solisLength - 1], fluxarray[fluxLength - 1], rollarray[rollLength - 1], gpsarray[gpslength -1])).tolist()
        dictionary = dict(zip(everything, value))
        jsonmess = json.dumps(dictionary, indent=4)
        print(jsonmess)
        s.sendto(jsonmess.encode(), (client,port))
        s2.sendto(jsonmess.encode(), (client2,port2))

        time.sleep(1)
    except OSError:
        pass
    except KeyboardInterrupt:
        break
    except Exception as e:
        print(e)
        #print(f"Exception happened {e}")
s.sendto("stop".encode(),(client,port))
#s.close()


Connected
['SAT1']
Client = 10.55.21.3,5005
Client = 10.55.11.44,5004
{
    "Time": "1 Jan 2024 18:50:14.000000000",
    "ODY EOM Summary Pos_CBIX": "-156.741689488537",
    "ODY EOM Summary Pos_CBIY": "-5826.17011516566",
    "ODY EOM Summary Pos_CBIZ": "3862.86103845672",
    "ODY EOM Summary SCRate_BDYX": "-0.00017105460167980382",
    "ODY EOM Summary SCRate_BDYY": "0.00010797074522453043",
    "ODY EOM Summary SCRate_BDYZ": "0.0012780935158515567",
    "ODY EOM Summary Vel_CBIX": "-1.35045163820124",
    "ODY EOM Summary Vel_CBIY": "-4.08854989315314",
    "ODY EOM Summary Vel_CBIZ": "-6.20567823752587",
    "STK BattSOC": "93.5394583987135",
    "STK Eclipse": "False",
    "STK GenPower": "33.389207402439844",
    "STK LoadPower": "29.22154325231059",
    "STK ModeString": "NORMAL_OPS: SunTrack (Clk: FrameFixed)",
    "ODY Panel SolarFlux SolarFluxSA_A_PZ": "31.5040855805865",
    "ODY Panel SunAngle SunAngleSA_A_PZ": "0.0024212251041866623",
    "ODY SA_B_NZ GimbalRate": "0.0",


Attach to STK

Open scenario

Create a satellite

Main Program

In [ ]:
sat = scenario.Children.Item("SAT1")
dataProvider = sat.DataProviders.Item("User Supplied Data")
powerFolder = dataProvider.Group.Item("SOLIS Simulation")
dynamicsFolder = dataProvider.Group.Item("ODySSy Dynamics")
fluxFolder = dataProvider.Group.Item("ODySSy Power Thermal")

timeData = dynamicsFolder.ExecElements(scenario.StartTime, scenario.StopTime, 1.0, ["Time"])
dyndata = dynamicsFolder.ExecElements(scenario.StartTime, scenario.StopTime, 1.0,['ODY EOM Summary Vel_CBIX',"ODY EOM Summary Vel_CBIY","ODY EOM Summary Vel_CBIZ","ODY EOM Summary Pos_CBIX","ODY EOM Summary Pos_CBIY","ODY EOM Summary Pos_CBIZ"])
powerdata = powerFolder.ExecElements(scenario.StartTime, scenario.StopTime, 1.0, ["STK BattSOC"])
timeArray = timeData.DataSets.ToNumpyArray()
length = len(timeArray)
dynArray = dyndata.DataSets.ToNumpyArray()
powerarray = powerdata.DataSets.ToNumpyArray()
lengthpower = len(powerarray)

totaldata = np.concatenate((timeArray[length-1], dynArray[length-1], powerarray[lengthpower-1]))
print("Total Data =",totaldata.tolist())

#print(timeArray[length-1])
#print(dynArray[length-1])
#print(powerarray[lengthpower-1])
#print(dynArray)

#posx = np.fromstring(str(dynArray[:,0]).strip("[]"), sep= " ")

#dataset = {"Time":str(timeArray),"PositionX":posx, "BattSOC":battsoc}
#print(dataset)

## Close Program

In [ ]:
stk.ShutDown()